In [1]:
from openbabel import pybel
from Bio.PDB import * 


In [2]:
import pandas as pd

In [3]:
df = pd.read_table('biolip/data/BioLiP_2013-03-6_nr.txt',sep='\t',header=None,usecols=[0,4,5,6,13,14,15,16,19])
df = df.rename(columns={0:'pdb',4:'chain',5:'l_id',6:'l_chain',
                        13: 'affinity_lit',14: 'affinity_moad',15: 'affinity_pdbbind-cn',16:'affinity_bindingdb',
                        19: 'seq'})

In [4]:
base = 'biolip/data/ligand_nr/'
df['ligand_fn'] = base + df['pdb']+'_'+df['chain']+'_'+df['l_id'].astype(str)+'_'+df['l_chain'].astype(str)+'.pdb'

In [5]:
df_complex = pd.read_parquet('data/biolip_complex.parquet')

In [97]:
df_affinity = df_complex[~df_complex['affinity_lit'].isnull() | ~df_complex['affinity_moad'].isnull() 
                         | ~df_complex['affinity_pdbbind-cn'].isnull() | ~df_complex['affinity_bindingdb'].isnull()].copy()

In [98]:
from pint import UnitRegistry
import numpy as np
import re
ureg = UnitRegistry()

def to_uM(affinities):
    lit, moad, pdbbind, bindingdb = affinities

    vals = []
    try:
        lit = re.split('[=~<>]',str(lit))[1].split(' ')[0]
        lit =  ureg(lit).m_as(ureg.uM)
        vals.append(lit)
    except:
        pass

    try:
        moad = re.split('[=~<>]',str(moad))[1].split(' ')[0]
        moad = ureg(moad).m_as(ureg.uM)
        vals.append(moad)
    except:
        pass

    try:
        pdbbind = re.split('[=~<>]',str(pdbbind))[1].split(' ')[0]
        pdbbind = ureg(bindingdb).m_as(ureg.uM)
        vals.append(pdbbind)
    except:
        pass

    try:
        bindingdb = re.split('[=~<>]',str(bindingdb))[1].split(' ')[0]
        bindingdb =  ureg(bindingdb).m_as(ureg.uM)
        vals.append(bindingdb)
    except:
        pass

    if len(vals) > 0:
        vals = np.array(vals)
        return np.mean(vals[~np.isnan(vals)])
    
    return None

In [99]:
df_affinity['affinity_uM'] = df_affinity[['affinity_lit','affinity_moad','affinity_pdbbind-cn','affinity_bindingdb']].apply(to_uM,axis=1)

In [101]:
df_affinity[~df_affinity['affinity_uM'].isnull()]

pdb chain l_id  l_chain affinity_lit                 affinity_moad  \
38      11gs   EAA    A        1         None            ki=1.5uM (GTT EAA)   
43      13gs   SAS    A        1         None                 ki=24uM (SAS)   
54      17gs   GTX    A        1         None                          None   
55      181l   BNZ    A        1         None             Ka=5700M^-1 (BNZ)   
56      182l   BZF    A        1         None             Ka=8900M^-1 (BZF)   
...      ...   ...  ...      ...          ...                           ...   
105087  8kme   III    3        1         None  ki=8uM (BNN CUC TRG LEU PRO)   
105088  8kme   III    4        1         None  ki=8uM (BNN CUC TRG LEU PRO)   
105106  966c   RS2    A        1         None                 ki=23nM (RS2)   
105124  9icd   NAP    A        1         None                kd=125uM (NAP)   
105138  9nse   ISU    B        2         None              Ki=0.039uM (ISU)   

       affinity_pdbbind-cn affinity_bindingdb  \
38      Ki=1.5uM (GTT-EAA)               None   
43           Ki=24uM (SAS)               None   
54                    None         Kd=10000nM   
55                    None        Kd=175000nM   
56                    None        Kd=112000nM   
...                    ...                ...   
105087                None               None   
105088                None               None   
105106       Ki=23nM (RS2)               None   
105124      Kd=125uM (NAP)               None   
105138                None               None   

                                                      seq  \
38      PYTVVYFPVRGRCAALRMLLADQGQSWKEEVVTVETWQEGSLKASC...   
43      MPPYTVVYFPVRGRCAALRMLLADQGQSWKEEVVTVETWQEGSLKA...   
54      MPPYTVVYFPVRGRCAALRMLLADQGQSWKEEVVTVETWQEGSLKA...   
55      MNIFEMLRIDEGLRLKIYKDTEGYYTIGIGHLLTKSPSLNAAKSEL...   
56      MNIFEMLRIDEGLRLKIYKDTEGYYTIGIGHLLTKSPSLNAAKSEL...   
...                                                   ...   
105087  IVEGSDAEIGMSPWQVMLFRKSPQELLCGASLISDRWVLTAAHCLL...   
105088  IVEGSDAEIGMSPWQVMLFRKSPQELLCGASLISDRWVLTAAHCLL...   
105106  RWEQTHLTYRIENYTPDLPRADVDHAIEKAFQLWSNVTPLTFTKVS...   
105124  SKVVVPAQGKKITLQNGKLNVPENPIIPYIEGDGIGVDVTPAMLKV...   
105138  KFPRVKNWELGSITYDTLCAQSQQDGPCTPRRCLGSLVLPRKLQTR...   

                                     ligand_fn  \
38      biolip/data/ligand_nr/11gs_EAA_A_1.pdb   
43      biolip/data/ligand_nr/13gs_SAS_A_1.pdb   
54      biolip/data/ligand_nr/17gs_GTX_A_1.pdb   
55      biolip/data/ligand_nr/181l_BNZ_A_1.pdb   
56      biolip/data/ligand_nr/182l_BZF_A_1.pdb   
...                                        ...   
105087  biolip/data/ligand_nr/8kme_III_3_1.pdb   
105088  biolip/data/ligand_nr/8kme_III_4_1.pdb   
105106  biolip/data/ligand_nr/966c_RS2_A_1.pdb   
105124  biolip/data/ligand_nr/9icd_NAP_A_1.pdb   
105138  biolip/data/ligand_nr/9nse_ISU_B_2.pdb   

                                                   smiles  affinity_uM  
38                CC[C@H](C(=O)c1ccc(c(c1Cl)Cl)OCC(=O)O)C        1.500  
43      OC(=O)c1cc(/N=N/c2ccc(cc2)S(=O)(=O)Nc2ccccn2)c...       24.000  
54      CCCCCCSC[C@@H](C(=O)NCC(=O)O)NC(=O)CC[C@@H](C(...       10.000  
55                                               c1ccccc1      175.000  
56                                        c1ccc2c(c1)occ2      112.000  
...                                                   ...          ...  
105087  O=C[C@@H](NC(=O)[C@H](Cc1ccc(cc1)OS(O)(O)O)NC(...        8.000  
105088  CC(C[C@@H](C(=O)N1C=CC[C@H]1C(=O)N)NC(=O)[C@@H...        8.000  
105106     ONC(=O)CC1(CCOCC1)S(=O)(=O)c1ccc(cc1)Oc1ccccc1        0.023  
105124  O[C@@H]1[C@@H](COP(=O)(O)O)O[C@H]([C@@H]1OP(=O...      125.000  
105138                                       CC[Se]C(=N)N        0.039  

[7588 rows x 12 columns]

In [102]:
df_affinity.to_parquet('data/biolip.parquet')